In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
import cv2
import numpy as np
import matplotlib.pyplot as plt
from keras.models import load_model
import keras
from matplotlib import animation, rc
from IPython.display import HTML
import moviepy.editor as mpy
from PIL import Image

# get frames

In [ ]:
siz=224
# resizing
def resize(source):
    source=np.array(source)
    if source.max()<=1:
        source=(source*255).astype(np.uint8)
    new = Image.fromarray(source)
    new=new.resize((siz,siz)).convert('RGB')
    new = np.array(new)
    if(new.max()>1):
        new=new/255
    return new

In [ ]:
temp = np.load('/content/drive/My Drive/research_by_03t_ericxiao_thomaswang/processed_data/data224.npz')
classname=temp['filename']
num_classes = len(classname)
print(num_classes,classname)

12 ['ambulance' 'river' 'helicopter' 'screaming' 'fire' 'lightning' 'typing'
 'cars' 'wave' 'cheer' 'writing' 'blender']


In [ ]:
path='/content/drive/My Drive/research_by_03t_ericxiao_thomaswang/videos/example224.mp4'
cap = cv2.VideoCapture(path)
frames=[]
cnt=1
fps=cap.get(cv2.CAP_PROP_FPS)
while True:
    if cnt%100==0:
        print("%5d"%cnt,end=' ')
        if cnt%2500==0:
            print()
    cnt+=1
    t=cap.read()
    if t[0]:
        t = cv2.cvtColor(t[1], cv2.COLOR_BGR2RGB)
        # t=compress(t)
        # plt.imshow(t)
        # plt.show()
        frames.append(t)
    else:
        break
frames=np.array(frames)
if(frames.max()>1):
    frames=frames/255
print('\nshape:',frames.shape)

  100   200   300   400   500   600   700   800   900  1000  1100  1200  1300  1400  1500  1600  1700  1800  1900  2000  2100  2200  2300  2400  2500 
 2600  2700  2800  2900  3000  3100 
shape: (3150, 224, 224, 3)


In [ ]:
# from moviepy.editor import ImageSequenceClip
# res=ImageSequenceClip(new, fps=24)
# res.write_videofile("result.mp4")
# import imageio
# imageio.mimwrite("result.mp4", (new*255).astype(np.uint8) , fps = 24)

# [moviepy](https://zulko.github.io/moviepy/)

In [ ]:
from moviepy.editor import AudioFileClip
audio = []
for i in range(len(classname)):
    audio.append(AudioFileClip('/content/drive/My Drive/research_by_03t_ericxiao_thomaswang/sound_effects/' + classname[i] + ".mp3"))

In [ ]:
model = load_model('/content/drive/My Drive/research_by_03t_ericxiao_thomaswang/saved_model/transfer-resnet152v2-pop0.h5')

In [ ]:
predict = model.predict(frames)

In [ ]:
consider_range=200
def get_label(i):
    cnt=np.ndarray(shape=(len(classname),))
    cnt.fill(0)
    for x in range(max(i-consider_range//2,0),min(i+consider_range//2,len(frames))):
        cnt[predict[x].argmax()]+=1
    return cnt.argmax()

In [ ]:
st=np.zeros((12,))
for i in range(len(predict)):
    # print(predict[i])
    st[get_label(i)]+=1
print()
for i in range(12):
    print(classname[i],': ',st[i]/len(predict),'%',sep='')

In [ ]:
from moviepy.editor import concatenate_audioclips,VideoFileClip
fps=24
clips=[]
i=0
labels=[get_label(i) for i in range(len(predict))]
while i<len(predict):
    l=i
    while i<len(predict) and labels[i]==labels[l]:
        i+=1
    while i-l>=audio[labels[l]].duration*fps:
        l+=int(audio[labels[l]].duration*fps)
        clips.append(audio[labels[l]])
    if i!=l:
        clips.append(audio[labels[l]].subclip(0,(i-l)/fps))
final = concatenate_audioclips(clips)
video = VideoFileClip(path)
video = video.set_audio(final)
video.write_videofile("result.mp4")
video.ipython_display(maxduration=10000)

[MoviePy] >>>> Building video result.mp4
[MoviePy] Writing audio in resultTEMP_MPY_wvf_snd.mp3


100%|██████████| 2896/2896 [00:05<00:00, 533.91it/s]

[MoviePy] Done.
[MoviePy] Writing video result.mp4



100%|█████████▉| 3150/3151 [00:04<00:00, 758.69it/s]

[MoviePy] Done.
[MoviePy] >>>> Video ready: result.mp4 




100%|█████████▉| 3150/3151 [00:02<00:00, 1551.27it/s]


In [ ]:
video.ipython_display(maxduration=10000)

# class defination

In [ ]:
class sound_effect():
    def __init__(self,verbose=1):
        from google.colab import drive
        drive.mount('/content/drive')
        self.verbose=1
        # import dependencies
        from moviepy.editor import AudioFileClip
        from keras.models import load_model
        import numpy as np
        self.siz=224
        # load class-names
        temp = np.load('/content/drive/My Drive/research_by_03t_ericxiao_thomaswang/processed_data/data224-20cat+none-filtered.npz')
        self.classname=temp['filename']
        if self.verbose==1:
            print('loading audios ...',end='')
        # load audios
        self.audio=[AudioFileClip('/content/drive/My Drive/research_by_03t_ericxiao_thomaswang/sound_effects/'+cn+'.mp3') for cn in self.classname]
        if self.verbose==1:
            print(' done !')
        # laod predicting model
        if self.verbose==1:
            print('loading predicting model ...',end='')
        self.model = load_model('/content/drive/My Drive/research_by_03t_ericxiao_thomaswang/saved_model/transfer-resnet152v2-dropout0.5-20cat+none+fine-tune.h5')
        if self.verbose==1:
            print(' done !')
        self.consider_range=1
    # define resizing fuction
    def resize(self,source):
        from PIL import Image
        import numpy as np
        source=np.array(source)
        if source.max()<=1:
            source=(source*255).astype(np.uint8)
        new = Image.fromarray(source)
        new=new.resize((self.siz,self.siz)).convert('RGB')
        new = np.array(new)
        if(new.max()>1):
            new=new/255
        return new
    def process(self,path,exclude=[]):
        from moviepy.editor import concatenate_audioclips,VideoFileClip
        import numpy as np
        import cv2
        import time
        start=time.time()
        if self.verbose==1:
            print('capturing frames ...',end='')
        cap = cv2.VideoCapture(path)
        self.frames=[]
        self.fps=cap.get(cv2.CAP_PROP_FPS)
        scale=int(self.fps)//10
        self.fps/=scale
        while True:
            for _ in range(scale):
                t=cap.read()
            if t[0]:
                t = cv2.cvtColor(t[1], cv2.COLOR_BGR2RGB)
                self.frames.append(self.resize(t))
            else:
                break
        self.frames=np.array(self.frames)
        if self.verbose==1:
            print(' done !')
        # predict
        if self.verbose==1:
            print('predicting ...',end='')
        self.predict = self.model.predict(self.frames)
        # del self.frames
        if self.verbose==1:
            print(' done !')
        if self.verbose==1:
            print('generating audios ...',end='')
        # define labeling fuction   
        def get_label(i):
            cnt=np.ndarray(shape=(len(self.classname),))
            cnt.fill(1)
            for x in range(max(i-int(self.consider_range*self.fps)//2,0),min(i+int(self.consider_range*self.fps)//2,len(self.predict))):
                cnt[self.predict[x].argmax()]+=1
            while self.classname[cnt.argmax()] in exclude:
                cnt[cnt.argmax()]=0
            return cnt.argmax()
        # get labels
        labels=[get_label(i) for i in range(len(self.predict))]
        # append audio clips
        clips=[]
        i=0
        while i<len(self.predict):
            l=i
            while i<len(self.predict) and labels[i]==labels[l]:
                i+=1
            while i-l>=self.audio[labels[l]].duration*self.fps:
                l+=int(self.audio[labels[l]].duration*self.fps)
                clips.append(self.audio[labels[l]])
            if i!=l:
                clips.append(self.audio[labels[l]].subclip(0,(i-l)/self.fps))
        # combine audios and video
        final = concatenate_audioclips(clips)
        video = VideoFileClip(path)
        video = video.set_audio(final)
        if self.verbose==1:
            print(' done !')
            print('finished in %.2fs'%(time.time()-start))
        return video
    def remove_audio(self,path,dst=None):
        if dst==None:
            dst=path
        from moviepy.editor import VideoFileClip
        video=VideoFileClip(path).without_audio()
        video.write_videofile(dst,verbose=False,progress_bar=False)
        return dst
effect = sound_effect()

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).
Imageio: 'ffmpeg-linux64-v3.3.1' was not found on your computer; downloading it now.
Try 1. Download from https://github.com/imageio/imageio-binaries/raw/master/ffmpeg/ffmpeg-linux64-v3.3.1 (43.8 MB)
Downloading: 8192/45929032 bytes (0.0%)1966080/45929032 bytes (4.3%)5726208/45929032 bytes (12.5%)9560064/45929032 bytes (20.8%)13443072/45929032 bytes (29.3%)17203200/45929032 bytes (37.5%)20987904/45929032 bytes (45.7%)24911872/45929032 bytes (54.2%)28844032/45929032 bytes (62.8%)32751616/45929032 bytes (71.3%)36667392/45929032 bytes (79.8%)

Using TensorFlow backend.


loading audios ... done !
loading predicting model ... done !


In [ ]:
# video.ipython_display()
video.write_videofile(folder+'result_of_'+path,verbose=False,progress_bar=False)

In [ ]:
folder='/content/drive/My Drive/research_by_03t_ericxiao_thomaswang/videos/'
path='Screaming People.mp4'
removed=effect.remove_audio(folder+path,folder+'no_audio_'+path)
video = effect.process(removed)
video.write_videofile(folder+'result_of_'+path,verbose=False,progress_bar=False)

capturing frames ... done !
predicting ... done !
generating audios ... done !
finished in 134.50s


In [ ]:
print(effect.classname[[i.argmax() for i in effect.predict]])

['screaming' 'screaming' 'cat_meowing' ... 'water_drop' 'water_drop'
 'water_drop']


In [ ]:
folder='/content/drive/My Drive/research_by_03t_ericxiao_thomaswang/videos/'
path='no_audio1.mp4'
video = effect.process(folder+path)
video.write_videofile(folder+'jizz.mp4',verbose=False,progress_bar=False)
# folder='/content/drive/My Drive/research_by_03t_ericxiao_thomaswang/videos/'
# path='no_audio2.mp4'
# video = effect.process(folder+path)
# video.write_videofile(folder+'video5.mp4',verbose=False,progress_bar=False)
# folder='/content/drive/My Drive/research_by_03t_ericxiao_thomaswang/videos/'
# path='no_audio3.mp4'
# video = effect.process(folder+path)
# video.write_videofile(folder+'video6.mp4',verbose=False,progress_bar=False)

capturing frames ... done !
predicting ... done !
generating audios ... done !
finished in 46.85s


In [ ]:
print((effect.classname))

['ambulance' 'river' 'helicopter' 'screaming' 'fire' 'lightning' 'typing'
 'cars' 'wave' 'cheer' 'writing' 'blender' 'cat_meowing' 'dog_barking'
 'door_opening' 'glass_breaking' 'high_heels' 'stars_shining'
 'train_passing' 'water_drop']


In [ ]:
# plt.figure(figsize=)
effect.predict=effect.blablabla()
fig,ax=plt.subplots(len(effect.classname),figsize=(15,5*len(effect.classname)))
for ind in range(len(effect.classname)):
    # ind=0
    ax[ind].set_title(effect.classname[ind])
    # ax[ind].set_ylim(0,1.0)
    ax[ind].set_xticks(np.linspace(0,video.duration,10).astype('int32'))
    ax[ind].plot(np.linspace(0,video.duration,len(effect.predict)),[effect.predict[i][ind] for i in range(len(effect.predict))])
plt.show()

In [ ]:
video.ipython_display(maxduration=10000)

In [ ]:
from moviepy.editor import VideoFileClip
path='/content/drive/My Drive/research_by_03t_ericxiao_thomaswang/videos/example224.mp4'
original=VideoFileClip(path)
original.ipython_display(maxduration=10000)

# matplotlib animation

In [ ]:
# fig,ax=plt.subplots()
# ax.axis('off')
# pict=ax.imshow(frames[0])
# text=ax.text(siz/2,siz-10,get_label(0),backgroundcolor='white',ha='center',va='center')
# plt.close()
# def animate(i):
#     i=int(i)
#     pict.set_data(frames[i])
#     text.set_text(classname[get_label(i)])
#     return (pict,text)
# anim = animation.FuncAnimation(fig, animate, frames=np.linspace(0,len(frames)-1,400), interval=60, blit=True)
# rc('animation', html='jshtml')
# anim

In [ ]:
anim.save('result.mp4')